# scan different paramters for the first high res registartion
This process takes a lot of time and should be done on a few parameters.


In [1]:
%load_ext autoreload
%autoreload 2
import os
import sys
import zarr
from pathlib import Path
import hjson
import numpy as np
from IPython.display import display, HTML
from tifffile import imread as tif_imread
from tifffile import imwrite as tif_imwrite

from tqdm.auto import tqdm
# Path for bigstream unless you did pip install
sys.path = ["/mnt/nasquatch/data/2p/jonna/Code_Python/Notebooks_Jonna/BigStream/bigstream_github"] + sys.path 
sys.path.append("../../")
from bigstream.align import feature_point_ransac_affine_align
from bigstream.application_pipelines import easifish_registration_pipeline 
from bigstream.transform import apply_transform
from registrations_funcs import HCR_confocal_imaging, register_lowres, verify_rounds

%load_ext autoreload
%autoreload 2




hjson_file = '/home/oamsalem/code/Projects/EZfish/ezfish_pipeline/examples/RG026.hjson'
manifest = hjson.load(open(hjson_file, 'r'))

output_folder = Path(manifest['base_path']) / manifest['mouse_name'] / 'OUTPUT' / 'HCR' / 'registrations' 

round_to_rounds, reference_round = verify_rounds(manifest)



The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
All files found
Rounds available for register:
02 ['DAPI', 'GLP1R', 'CHAT', 'TAC1']
03 ['DAPI', 'RORB', 'NPR3', 'VGAT']


### PARAMETERS

In [7]:
# Choose the round to register
HCR_round_to_register = '03'# 02,03...?

assert HCR_round_to_register in round_to_rounds.keys(), f"round {HCR_round_to_register} not found in rounds to register"



### Image parameters 

In [8]:
mov_round = round_to_rounds[HCR_round_to_register]
# File names
HCR_fix_image_path = reference_round['image_path'] # The fix image that all other rounds will be registerd to (include all channels!)
HCR_mov_image_path = mov_round['image_path'] # The image that will be registered to the fix image (include all channels!)

round_folder_name = f"HCR{HCR_round_to_register}_to_HCR{reference_round['round']}"

# resolution of the images
fix_image_spacing = np.array(reference_round['resolution']) # Y,X,Z
mov_image_spacing = np.array(mov_round['resolution']) # Y,X,Z

# spatial downsampling, probably no need to test. (Changed x and y from 3 to 2 for CIM round 5)
red_mut_x = 2 
red_mut_y = 2
red_mut_z = 2


### bigstream parameters (Pick what seems to have been good from 1_scan_lowres_parameters, 1 set)

In [9]:
### Global parameters ###
## These should be scanned in the 1_scan_lowres_parameters notebook, should use only 1 set here##

# radius for local ransac for each spot (in pixles for LOW res image) - how many pixels to look around a spot for match
g_radii_z = [1]
g_radii_xy = [25]

# when searching for blobs for ransac, what is the radius for the search alogorithem (in pixles for low res image)
g_bsize_s_b = [[3,30]]

# what is the minumum correlation for a spot to be considered a match
g_m_tresholds = [0.2] 

### Local parameters ###

# block size for local affine and deformable registration # [[x,y,z]]
blocksize_to_scan = [[50,50,12],[100, 100, 25]]

# Radius for local RANSAC for each spot (in pixels for high res image) - how many pixels to look around a spot for match
radii_z = [1, 5, 10]
radii_xy = [15,25, 50]
bsize_s_b = [[5, 70]]
m_tresholds = [0.2]

# Example configurations
# [z = 3, xy = 15, 3,20 bs, th = 0.2] # RG002
# [z = 1, xy = 25, 3,20 bs, th = 0.2] # CIM132


#### Load the images

In [10]:
# Take first channel, I always assume that the first channel is what we want to register
fix_highres = tif_imread(HCR_fix_image_path)[:,0].transpose(2,1,0) # take first channlel and transform from Z,X,Y to Y,X,Z
mov_highres = tif_imread(HCR_mov_image_path)[:,0].transpose(2,1,0) # take first channlel and transform from Z,X,Y to Y,X,Z


fix_lowres = fix_highres[::red_mut_y,::red_mut_x,::red_mut_z]
fix_lowres_spacing = fix_image_spacing * np.array([red_mut_y,red_mut_x,red_mut_z])


mov_lowres = mov_highres[::red_mut_y,::red_mut_x,::red_mut_z]
mov_lowres_spacing = mov_image_spacing * np.array([red_mut_y,red_mut_x,red_mut_z])

# Print the dimensions of the high-resolution and low-resolution images
print(f"The dimensions of the high-resolution fixed image are: {fix_highres.shape}")
print(f"The dimensions of the high-resolution moving image are: {mov_highres.shape}")
print(f"The dimensions of the low-resolution moving image are: {mov_lowres.shape}")

The dimensions of the high-resolution fixed image are: (2922, 2914, 71)
The dimensions of the high-resolution moving image are: (3104, 3104, 89)
The dimensions of the low-resolution moving image are: (1552, 1552, 45)


In [11]:
c = {'n_workers': 15, 'threads_per_worker':2} # Colab00 has 20 cores, 2 threads per core, leave a little wiggle room, added c to args. Camillo has 40 cores.

success_n = 0
write_dir = output_folder / round_folder_name / 'local_params_scan'
write_dir.mkdir(exist_ok=True,parents=True)
write_directory = str(write_dir)
print(write_directory)

#Change this when ready to proceed with full reg! and change params up top before doing so
no_deform = True

if no_deform:
    write_dir = write_dir.parent / f'{write_dir.name}_nodeform'

njobs = len(g_radii_z)*len(g_radii_xy)*len(g_bsize_s_b)*len(g_m_tresholds)*len(blocksize_to_scan)*len(radii_z)*len(radii_xy)*len(bsize_s_b)*len(m_tresholds)
pbar = tqdm(total=njobs)
for g_radius_z in g_radii_z:
  for g_radius_xy in g_radii_xy:
    for g_bsize_s, g_bsize_b in g_bsize_s_b:
      for g_m_treshold in g_m_tresholds:
        for blocksize in blocksize_to_scan:
          for radius_z in radii_z:
            for radius_xy in radii_xy:
              for bsize_s, bsize_b in bsize_s_b:
                for m_treshold in m_tresholds:
                        
                  # wrong folder nameing need to replace the name
                  local_folder = fr"rz{g_radius_z}_rxy{g_radius_xy}_bs{g_bsize_s}to{g_bsize_b}_mt{g_m_treshold}"
                  global_folder = fr"bs{blocksize[0]}_{blocksize[1]}_{blocksize[2]}_{radius_z}_{radius_xy}_bs{bsize_s}to{bsize_b}_mt{m_treshold}"

                  write_directory = write_dir / local_folder / global_folder
                  write_directory.mkdir(exist_ok=True,parents=True)
                  write_directory = str(write_directory); print(write_directory)

                  global_ransac_kwargs = {'cc_radius':(g_radius_xy,g_radius_xy,g_radius_z),
                                          'blob_sizes':[g_bsize_s, g_bsize_b],
                                          'match_threshold':g_m_treshold}

                  local_ransac_kwargs = {'cc_radius':(radius_xy,radius_xy,radius_z),
                                               'blob_sizes':[bsize_s, bsize_b], 
                                               'match_threshold': [m_treshold]}
                    
                
                  
                  affine, deform, aligned = easifish_registration_pipeline(
                          fix_lowres, fix_highres, mov_lowres, mov_highres,
                          fix_lowres_spacing, fix_image_spacing,
                          mov_lowres_spacing, mov_image_spacing,
                          blocksize=blocksize,
                          global_ransac_kwargs=global_ransac_kwargs,
                          local_ransac_kwargs=local_ransac_kwargs,
                          write_directory=write_directory,
                          no_deform=no_deform,
                          overwrite_lowres=False,
                          c = c)
                  print(f'finished! - {write_directory}')
                  pbar.update(1)

/mnt/bananas/data/ezfish/jonna/RG026/OUTPUT/HCR/registrations/HCR03_to_HCR01/local_params_scan


  0%|          | 0/18 [00:00<?, ?it/s]

/mnt/bananas/data/ezfish/jonna/RG026/OUTPUT/HCR/registrations/HCR03_to_HCR01/local_params_scan_nodeform/rz1_rxy25_bs3to30_mt0.2/bs50_50_12_1_15_bs5to70_mt0.2
Fri Aug 16 13:26:33 2024 Run ransac {'alignment_spacing': 12.12, 'blob_sizes': [3, 30], 'cc_radius': (25, 25, 1), 'match_threshold': 0.2}
Fri Aug 16 13:26:33 2024 computing fixed spots
Fri Aug 16 13:26:33 2024 fixed spots detection using {'num_sigma': 15, 'exclude_border': (25, 25, 1)}
Fri Aug 16 13:26:33 2024 Start spot detection ((3, 3, 3), (30, 30, 30)) {'exclude_border': (25, 25, 1), 'num_sigma': 15, 'min_sigma': array([1.73205081, 1.73205081, 1.73205081]), 'max_sigma': array([17.32050808, 17.32050808, 17.32050808]), 'threshold': None, 'threshold_rel': 0.1}
Fri Aug 16 13:27:08 2024 Spot detection ((3, 3, 3), (30, 30, 30)) completed in 34.558908462524414s
Fri Aug 16 13:27:08 2024 found 3678 fixed spots
Fri Aug 16 13:27:08 2024 computing moving spots
Fri Aug 16 13:27:08 2024 moving spots detection using {'num_sigma': 15, 'exclud

/mnt/nasquatch/data/2p/jonna/Code_Python/Notebooks_Jonna/BigStream/bigstream_github/bigstream/piecewise_align.py:373: RuntimeWarning: invalid value encountered in divide
  weights = weights / (1 - missing_weights)


Fri Aug 16 13:38:22 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 2.157956838607788s
Fri Aug 16 13:38:22 2024 found 0 fixed spots
Fri Aug 16 13:38:22 2024 insufficient fixed spots found
returning default
WRITING BLOCK (0, 0, 0) at Fri Aug 16 13:38:22 2024


...

FINISHED WRITING BLOCK (20, 45, 1) at Fri Aug 16 14:47:12 2024
WRITING BLOCK (20, 45, 2) at Fri Aug 16 14:47:12 2024Block index:  (20, 45, 3) 
Slices:  (slice(975, 1075, None), slice(2225, 2325, None), slice(30, 54, None))

Fri Aug 16 14:47:12 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 3.476747751235962s
Fri Aug 16 14:47:12 2024 found 9 fixed spots
Fri Aug 16 14:47:12 2024 insufficient fixed spots found
returning default
Fri Aug 16 14:47:12 2024 Run ransac {'blob_sizes': [5, 70], 'cc_radius': (15, 15, 1), 'match_threshold': [0.2], 'safeguard_exceptions': False}
Fri Aug 16 14:47:12 2024 computing fixed spots
Fri Aug 16 14:47:12 2024 fixed spots detection using {'num_sigma': 15, 'exclude_border': (15, 15, 1)}
Fri Aug 16 14:47:12 2024 Start spot detection ((5, 5, 5), (70, 70, 70)) {'exclude_border': (15, 15, 1), 'num_sigma': 15, 'min_sigma': array([2.88675135, 2.88675135, 2.88675135]), 'max_sigma': array([40.41451884, 40.41451884, 40.41451884]), 'threshold': None, 'thresho

/mnt/nasquatch/data/2p/jonna/Code_Python/Notebooks_Jonna/BigStream/bigstream_github/bigstream/piecewise_align.py:373: RuntimeWarning: invalid value encountered in divide
  weights = weights / (1 - missing_weights)


Fri Aug 16 14:47:17 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 3.9144673347473145s
Fri Aug 16 14:47:17 2024 found 10 fixed spots
Fri Aug 16 14:47:17 2024 insufficient fixed spots found
returning default
Fri Aug 16 14:47:18 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 3.958890199661255s
Fri Aug 16 14:47:18 2024 found 4 fixed spots
Fri Aug 16 14:47:18 2024 insufficient fixed spots found
returning default
Fri Aug 16 14:47:18 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 3.0280940532684326s
Fri Aug 16 14:47:18 2024 found 5 fixed spots
Fri Aug 16 14:47:18 2024 insufficient fixed spots found
returning default
WRITING BLOCK (56, 9, 0) at Fri Aug 16 14:47:18 2024
Fri Aug 16 14:47:18 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 4.0870890617370605s
Fri Aug 16 14:47:18 2024 found 9 fixed spots
Fri Aug 16 14:47:18 2024 insufficient fixed spots found
returning default


/mnt/nasquatch/data/2p/jonna/Code_Python/Notebooks_Jonna/BigStream/bigstream_github/bigstream/piecewise_align.py:373: RuntimeWarning: invalid value encountered in divide
  weights = weights / (1 - missing_weights)


Fri Aug 16 14:47:18 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 4.001651763916016s
Fri Aug 16 14:47:18 2024 found 18 fixed spots
Fri Aug 16 14:47:18 2024 insufficient fixed spots found
returning default
FINISHED WRITING BLOCK (5, 2, 4) at Fri Aug 16 14:47:18 2024
Block index:  (5, 3, 0) 
Slices:  (slice(225, 325, None), slice(125, 225, None), slice(0, 18, None))
WRITING BLOCK (5, 2, 5) at Fri Aug 16 14:47:18 2024
Fri Aug 16 14:47:18 2024 Spot detection ((5, 5, 5), (70, 70, 70)) completed in 3.9897217750549316s
Fri Aug 16 14:47:18 2024 found 27 fixed spots
Fri Aug 16 14:47:18 2024 insufficient fixed spots found
returning default
Fri Aug 16 14:47:18 2024 Run ransac {'blob_sizes': [5, 70], 'cc_radius': (15, 15, 1), 'match_threshold': [0.2], 'safeguard_exceptions': False}
Fri Aug 16 14:47:19 2024 computing fixed spots
Fri Aug 16 14:47:19 2024 fixed spots detection using {'num_sigma': 15, 'exclude_border': (15, 15, 1)}
Fri Aug 16 14:47:19 2024 Start spot detection ((5, 5, 5),

In [20]:
import os
os.getlogin()

'oamsalem'

In [ ]:
import os
import zarr
from tifffile import imwrite as tiff_imwrite

write_directory = fr"\mnt\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan\rz1_rxy25_bs3to30_mt0.2\bs100_100_25_1_25_bs5to70_mt0.2"
zarr_dir =  fr"\mnt\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan\rz1_rxy25_bs3to30_mt0.2\bs100_100_25_1_25_bs5to70_mt0.2\deformed.zarr"

# Check if the Zarr directory exists
if os.path.isdir(zarr_dir):
    print("Zarr directory exists")

    try:
        # Attempt to load the Zarr data
        data = zarr.open_array(zarr_dir, mode='r')
        print(f"Data loaded with shape: {data.shape}")
        
        if data is not None:
            # Save to TIFF file
            tiff_path = os.path.join(write_directory, "deformed.tiff")
            tiff_imwrite(tiff_path, data.transpose(2, 1, 0))
            print(f"TIFF file written successfully at {tiff_path}")
        else:
            print("Failed to load data. It is None.")
    except Exception as e:
        print(f"An error occurred while processing the Zarr data: {e}")
else:
    print("Zarr directory does not exist.")





In [ ]:
## Make combined TIFFs in new folder to check local parameter search

In [4]:
## If scanning local parameters (WITHOUT DEFORM), go through a master folder and turn all deformed.zarr into TIFFs and combine with original DAPI for ease of comparison.
#In future, save only non-degenerate affines would make this way easier.

import os
import zarr
import tifffile
import numpy as np
from tqdm import tqdm
import SimpleITK as sitk

def get_registration_score(fixed, mov):
    fixed_image = sitk.GetImageFromArray(fixed.astype(np.float32))
    registered_image = sitk.GetImageFromArray(mov.astype(np.float32))
    # Initialize the registration method
    irm = sitk.ImageRegistrationMethod()

    # Set the metric to ANTS Neighborhood Correlation
    irm.SetMetricAsMattesMutualInformation()  # 4 is the radius of the neighborhood

    # Set the fixed and moving images for the metric evaluation
    out = irm.MetricEvaluate(fixed_image,registered_image)
    return out

def find_folders_with_zarr(master_folder):
    zarr_folders = []
    for root, dirs, files in os.walk(master_folder):
        if 'deformed.zarr' in dirs:
            zarr_folders.append(root)
    return zarr_folders

def process_zarr_to_tiff(master_folder, dapi_file, subsample_z =2 ):
    zarr_folders = find_folders_with_zarr(master_folder)
    subfolder_count = len(zarr_folders)

    if subfolder_count == 0:
        print("No folders with 'deformed.zarr' found.")
        return

    print(f"Found {subfolder_count} folders with 'deformed.zarr'")
    print("Folders to process:", zarr_folders)

    output_dir = os.path.join(master_folder, 'tiff_outputs_gpt')
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    dapi_data = tifffile.imread(dapi_file)
    dapi_data = dapi_data.transpose(2, 1, 0)
    dapi_data_org = dapi_data.copy()
    dapi_data = dapi_data[:, :, ::subsample_z]

    pbar = tqdm(total=subfolder_count, desc="Processing folders")

    for index, zarr_folder in enumerate(zarr_folders):
        print(f"Processing folder {index + 1} out of {subfolder_count}")
        zarr_path = os.path.join(zarr_folder, 'deformed.zarr')
        subfolder_name = os.path.basename(zarr_folder)

        try:
            data = zarr.load(zarr_path)
#             from IPython import embed; embed()
            reg_score= get_registration_score(data, dapi_data_org)
            reg_score_text = str(np.round(reg_score,3)).replace('-','m')
        
            data = data[:, :, ::subsample_z]

            print(f"Zarr data shape: {data.shape}, DAPI data shape: {dapi_data.shape}")

            if data.shape != dapi_data.shape:
                print(f"Skipping {zarr_path} due to shape mismatch with DAPI data")
                pbar.update(1)
                continue

            combined_data = np.stack((dapi_data, data), axis=-1)
            print(f"Combined data shape before reshaping: {combined_data.shape}")

            tiff_path = os.path.join(output_dir, f"{reg_score_text}_{subfolder_name}_both.tiff")
            combined_data = combined_data.transpose(2, 3, 0, 1)
            tifffile.imwrite(tiff_path, combined_data, photometric='minisblack', imagej=True)

            print(f"Converted {zarr_path} to {tiff_path}")

        except Exception as e:
            print(f"Error processing {zarr_path}: {e}")

        pbar.update(1)
    
        # Add a check to break out of the loop if it stalls.

    pbar.close()

master_folder = fr"\\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2"
dapi_file =fr"\\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\CIM132_SLICE001_HCR1_C1_DAPI.tif"

process_zarr_to_tiff(master_folder, dapi_file)


Found 18 folders with 'deformed.zarr'
Folders to process: ['\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\240408_CIM132\\output_HCR4_to_HCR1_github\\local_params_scan_nodeform\\rz1_rxy25_bs3to30_mt0.2\\bs50_50_12_10_15_bs5to70_mt0.2', '\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\240408_CIM132\\output_HCR4_to_HCR1_github\\local_params_scan_nodeform\\rz1_rxy25_bs3to30_mt0.2\\bs50_50_12_1_15_bs5to70_mt0.2', '\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\240408_CIM132\\output_HCR4_to_HCR1_github\\local_params_scan_nodeform\\rz1_rxy25_bs3to30_mt0.2\\bs100_100_25_1_50_bs5to70_mt0.2', '\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\240408_CIM132\\output_HCR4_to_HCR1_github\\local_params_scan_nodeform\\rz1_rxy25_bs3to30_mt0.2\\bs100_100_25_10_15_bs5to70_mt0.2', '\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\240408_CIM132\\output_HCR4_to_HCR1_github\\local_params_scan_nodeform\\rz1_rxy25_bs3to30_mt0.2\\bs100_100_25_1_25_bs5to70_mt0.2', '\\\\bananas\\data\\ezfish\\jonna\\CIM132\\HCR\\24040

Processing folders:   0%|                                                                       | 0/18 [00:00<?, ?it/s]

Processing folder 1 out of 18
Zarr data shape: (1969, 1930, 39), DAPI data shape: (1969, 1930, 39)
Combined data shape before reshaping: (1969, 1930, 39, 2)


Processing folders:   6%|███▍                                                          | 1/18 [03:15<55:29, 195.86s/it]

Converted \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\bs50_50_12_10_15_bs5to70_mt0.2\deformed.zarr to \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\tiff_outputs_gpt\m0.215_bs50_50_12_10_15_bs5to70_mt0.2_both.tiff
Processing folder 2 out of 18
Zarr data shape: (1969, 1930, 39), DAPI data shape: (1969, 1930, 39)
Combined data shape before reshaping: (1969, 1930, 39, 2)


...

Converted \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\bs50_50_12_5_50_bs5to70_mt0.2\deformed.zarr to \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\tiff_outputs_gpt\m0.215_bs50_50_12_5_50_bs5to70_mt0.2_both.tiff
Processing folder 17 out of 18
Zarr data shape: (1969, 1930, 39), DAPI data shape: (1969, 1930, 39)
Combined data shape before reshaping: (1969, 1930, 39, 2)


Processing folders:  94%|█████████████████████████████████████████████████████████▌   | 17/18 [39:24<03:18, 198.16s/it]

Converted \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\bs50_50_12_5_25_bs5to70_mt0.2\deformed.zarr to \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\tiff_outputs_gpt\m0.215_bs50_50_12_5_25_bs5to70_mt0.2_both.tiff
Processing folder 18 out of 18
Zarr data shape: (1969, 1930, 39), DAPI data shape: (1969, 1930, 39)
Combined data shape before reshaping: (1969, 1930, 39, 2)


Processing folders: 100%|█████████████████████████████████████████████████████████████| 18/18 [40:29<00:00, 134.96s/it]

Converted \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\bs100_100_25_5_15_bs5to70_mt0.2\deformed.zarr to \\bananas\data\ezfish\jonna\CIM132\HCR\240408_CIM132\output_HCR4_to_HCR1_github\local_params_scan_nodeform\rz1_rxy25_bs3to30_mt0.2\tiff_outputs_gpt\m0.298_bs100_100_25_5_15_bs5to70_mt0.2_both.tiff
